In [1]:
import math
import numpy as np
from sympy import *
import plotly.graph_objects as go
import plotly.express as px

In [2]:
# зададим класс, совершающий всю работу над функциями
class TestFunctions():
  def __init__(self):
    # Подготовим символы для символьного вычисления sympy
    self.sympolic_x, self.sympolic_y = symbols("x y") 

    self.X_idx = 0
    self.Y_idx = 1
    self.left_def = 0
    self.right_def = 1
    

  def illustrate_func(self):
    """
    Иллюстрирует функцию в графике plotly
    """
    x_definability, y_definability = self.definability_of_func()[self.X_idx], self.definability_of_func()[self.Y_idx]
    x_values = np.arange(x_definability[self.left_def], x_definability[self.right_def])
    y_values = np.arange(y_definability[self.left_def], y_definability[self.right_def])

    z_values = []
    for xs in x_values:
      values = []
      for ys in y_values:
        values.append(self.func_definition(xs,ys))
      z_values.append(values)

    fig = go.Figure(data=[go.Surface(z=z_values, x=x_values, y=y_values)])
    fig.update_layout(title=self.get_name())
    fig.show()

  def get_name(self):
    pass

  def definability_of_func(self):
    """
    Метод выдает 2 параметра: левая и правая граница определения функции.
    Если присутствует x и y, то будет массив, где будет сначала x, потом y.
    """
    pass

  def func_definition(self, x, y):
    """
    Определение самой функции. Выдается значение для 3-х мерной функции.
    То есть выдается Z
    """
    pass

  def show_history_GD(self, history, n_x_samples = 100, n_y_samples = 100):
    """Формирует график истории формирования градиентного спуска на базе функции,
    которая генерирует историю изменения градиента.

    Args:
        history: История, после использования метода оптимизации, который возвращает объект вида:
          history = {'x': some array,
               'y': some array,
               'z': some array}
        n_x_samples (int, optional): Количество точек по оси X, которые необходимо отрисовать на графике. Defaults to 100.
        n_y_samples (int, optional): Количество точек по оси Y, которые необходимо отрисовать на графике. Defaults to 100.
    """
    x, y = symbols("x y") 

    x_definability, y_definability = self.definability_of_func()[self.X_idx], self.definability_of_func()[self.Y_idx]
    x_linspace = np.linspace(x_definability[self.left_def], x_definability[self.right_def], n_x_samples)
    y_linspace = np.linspace(y_definability[self.left_def], y_definability[self.right_def], n_y_samples)

    xx, yy = np.meshgrid(x_linspace, y_linspace)

    fxy = lambdify((x, y), self.sympolic_func_defifnition, 'numpy')
    zz = fxy(xx, yy)

    line = go.Scatter3d(x=history['x'], 
                        y=history['y'], 
                        z=history['z'], 
                        mode='lines', 
                        line=dict(
                            color='green',
                            width=10
                        ))
    
    surface = go.Surface(x = xx, y = yy, z = zz)
    
    frames = []
    for i in range(len(history['z'])):
        frames.append(go.Frame(data=[go.Scatter3d(x=[history['x'][i]], 
                                                  y=[history['y'][i]], 
                                                  z=[history['z'][i]],
                                                  mode="markers",
                                                  marker=dict(color="cyan", size=5))]))
    
    fig = go.Figure(data = [surface, line, surface], frames = frames,
            layout=go.Layout(
            xaxis=dict(range=[0, 5], autorange=False),
            yaxis=dict(range=[0, 5], autorange=False),

            updatemenus=[dict(
                type="buttons",
                buttons=[
                    dict(label="Play",
                         method="animate",
                         args=[None, 
                               {"frame": {"duration": 500}}])])]))
    fig.update_layout(title=self.get_name()+": анимация оптимизации")
    fig.show()

In [3]:


# зададим функции оптимизации
class IsomaClass(TestFunctions):
  def __init__(self):
    super().__init__()
    self.global_min_x = math.pi
    self.global_min_y = math.pi
    self.global_min_value = -1

    self.sympolic_func_defifnition = -cos(self.sympolic_x) * cos(self.sympolic_y) * exp(- ((self.sympolic_x - pi)**2 + (self.sympolic_y - pi)**2) )
    
  def definability_of_func(self):
    return ([-100, 100], [-100, 100])
  def get_name(self):
    return "Изома функция"

  def func_definition(self, x, y):
    return -np.cos(x) * np.cos(y) * np.exp(- (np.square(x - np.pi) + np.square(y - np.pi)) )


class MatiasClass(TestFunctions):
  def __init__(self):
    super().__init__()
    self.global_min_x = 0
    self.global_min_y = 0
    self.global_min_value = 0

    self.sympolic_func_defifnition = 0.26*((self.sympolic_x)**2 + (self.sympolic_y)**2) - 0.48*self.sympolic_x*self.sympolic_y

  def definability_of_func(self):
    return ([-10, 10], [-10, 10])
  def get_name(self):
    return "Функция Матьяса"
  def func_definition(self, x, y):
    return 0.26*(np.square(x) + np.square(y)) - 0.48*x*y

In [4]:
# нарисуем эти функции через plotly

isoma_func = IsomaClass()
isoma_func.illustrate_func()

In [5]:
matias_function = MatiasClass()
matias_function.illustrate_func()

In [6]:
# зададим вспомогательные функции
x, y = symbols("x y") 

def symbolic_diff(function, param, x_value, y_value):
    return float(function.diff(param).subs([(x, x_value), (y, y_value)]))

def numeric_diff(function, param, x_value, y_value, d_param):
    if param == x:
        return float((function.subs([(x, x_value + d_param), (y, y_value)]) + function.subs([(x, x_value - d_param), (y, y_value)])) / (2 * d_param))
    elif param == y:
        return float((function.subs([(x, x_value), (y, y_value + d_param)]) + function.subs([(x, x_value), (y, y_value - d_param)])) / (2 * d_param))

def gradient_magitude(x_diff, y_diff):
    return math.sqrt(x_diff ** 2 + y_diff ** 2)

def min_random_start(function, x_min, x_max, y_min, y_max, n_points = 10):
    random_x = np.random.uniform(x_min, x_max, n_points)
    random_y = np.random.uniform(y_min, y_max, n_points)

    xx, yy = np.meshgrid(random_x, random_y)
    fxy = lambdify((x, y), function, 'numpy')
    zz = fxy(xx, yy)

    min_indexes = np.unravel_index(zz.argmin(), zz.shape)

    return random_x[min_indexes[0]], random_y[min_indexes[1]]

In [7]:
x, y = symbols("x y") 

# Опишем различные варианты градиентного спуска
def GD(function, start_x, start_y, lr, n_iter, use_symbolic_grad = True, h = 0.001, use_decay_lr = False, decay_factor = 0.9):
    history = {'x': [start_x],
               'y': [start_y],
               'z': [float(function.subs([(x, start_x), (y, start_y)]))]}
    for _ in range(n_iter):
        if use_symbolic_grad:
            step_x = -lr * symbolic_diff(function, x, history['x'][-1], history['y'][-1])
            step_y = -lr * symbolic_diff(function, y, history['x'][-1], history['y'][-1])
        else:
            step_x = -lr * numeric_diff(function, x, history['x'][-1], history['y'][-1], h)
            step_y = -lr * numeric_diff(function, y, history['x'][-1], history['y'][-1], h)

        next_x = history['x'][-1] + step_x
        next_y = history['y'][-1] + step_y

        if next_x == start_x and next_y == start_y:
            print(f"Your gradient in {start_x};{start_y} is 0!")
            return history

        history['x'].append(next_x)
        history['y'].append(next_y)
        history['z'].append(float(function.subs([(x, next_x), (y, next_y)])))

        if use_decay_lr:
            lr *= decay_factor

    return history

def AGD_nesterov_momentum(function, start_x, start_y, lr, n_iter, beta = 0.9, use_symbolic_grad = True, h = 0.001, use_decay_lr = False, decay_factor = 0.9):
    history = {'x': [start_x],
               'y': [start_y],
               'z': [float(function.subs([(x, start_x), (y, start_y)]))]}
    
    if use_symbolic_grad:
        v_x = -lr * symbolic_diff(function, x, history['x'][-1], history['y'][-1])
        v_y = -lr * symbolic_diff(function, y, history['x'][-1], history['y'][-1])
    else:
        v_x = -lr * numeric_diff(function, x, history['x'][-1], history['y'][-1], h)
        v_y = -lr * numeric_diff(function, y, history['x'][-1], history['y'][-1], h)
        
    for _ in range(n_iter):
        if use_symbolic_grad:
            v_x = beta * v_x - lr * symbolic_diff(function, x, history['x'][-1] + v_x, history['y'][-1] + v_y)
            v_y = beta * v_y - lr * symbolic_diff(function, y, history['x'][-1] + v_x, history['y'][-1] + v_y)
        else:
            step_x = -lr * numeric_diff(function, x, history['x'][-1], history['y'][-1], h)
            step_y = -lr * numeric_diff(function, y, history['x'][-1], history['y'][-1], h)

        next_x = history['x'][-1] + v_x
        next_y = history['y'][-1] + v_y

        if next_x == start_x and next_y == start_y:
            print(f"Your gradient in {start_x};{start_y} is 0!")
            return history

        history['x'].append(next_x)
        history['y'].append(next_y)
        history['z'].append(float(function.subs([(x, next_x), (y, next_y)])))

        if use_decay_lr:
            lr *= decay_factor

    return history

def RMSProp(function, start_x, start_y, lr, n_iter, gamma = 0.1, use_symbolic_grad = True, h = 0.001, use_decay_lr = False, decay_factor = 0.9):
    e = 1e-7
    
    history = {'x': [start_x],
               'y': [start_y],
               'z': [float(function.subs([(x, start_x), (y, start_y)]))]}
    
    if use_symbolic_grad:
        G = gradient_magitude(symbolic_diff(function, x, history['x'][-1], history['y'][-1]), 
                              symbolic_diff(function, y, history['x'][-1], history['y'][-1]))
    else:
        G = gradient_magitude(numeric_diff(function, x, history['x'][-1], history['y'][-1], h), 
                              numeric_diff(function, y, history['x'][-1], history['y'][-1], h))
    
    for _ in range(n_iter):
        if use_symbolic_grad:
            G = gamma * G + (1 - gamma) * gradient_magitude(symbolic_diff(function, x, history['x'][-1], history['y'][-1]), 
                                                            symbolic_diff(function, y, history['x'][-1], history['y'][-1]))
        else:
            G = gamma * G + (1 - gamma) * gradient_magitude(numeric_diff(function, x, history['x'][-1], history['y'][-1], h), 
                                                            numeric_diff(function, y, history['x'][-1], history['y'][-1], h))
        
        if use_symbolic_grad:
            step_x = (-lr * symbolic_diff(function, x, history['x'][-1], history['y'][-1])) / math.sqrt(G + e)
            step_y = (-lr * symbolic_diff(function, y, history['x'][-1], history['y'][-1])) / math.sqrt(G + e)
        else:
            step_x = (-lr * numeric_diff(function, x, history['x'][-1], history['y'][-1], h)) / math.sqrt(G + e)
            step_y = (-lr * numeric_diff(function, y, history['x'][-1], history['y'][-1], h)) / math.sqrt(G + e)

        next_x = history['x'][-1] + step_x
        next_y = history['y'][-1] + step_y

        if next_x == start_x and next_y == start_y:
            print(f"Your gradient in {start_x};{start_y} is 0!")
            return history

        history['x'].append(next_x)
        history['y'].append(next_y)
        history['z'].append(float(function.subs([(x, next_x), (y, next_y)])))

        if use_decay_lr:
            lr *= decay_factor

    return history

In [8]:
history = RMSProp(isoma_func.sympolic_func_defifnition, 50, 50, 0.1, 100)
isoma_func.show_history_GD(history)

Your gradient in 50;50 is 0!


Функция Изома не дала результатов, так как у этой функции невозможно получить в любой ее точке не нулевой градиент. Из-за чего градиентные методы для этой функции не работают.

In [9]:
history = RMSProp(isoma_func.sympolic_func_defifnition, 2, 4, 0.1, 100)
isoma_func.show_history_GD(history)

При этом, если стартовая точка будет прям у начала пика вниз, то алгоритм, что очевидно, хорошо отрабатывает, так как там уже можно получить не нулевой градиент.

In [10]:
history = RMSProp(matias_function.sympolic_func_defifnition, 10, -10, 0.5, 100, use_decay_lr=True)
matias_function.show_history_GD(history)

In [11]:
history = AGD_nesterov_momentum(matias_function.sympolic_func_defifnition, 10, -10, 0.1, 100, beta=0.5, use_decay_lr=True)
matias_function.show_history_GD(history)

In [12]:
history = AGD_nesterov_momentum(matias_function.sympolic_func_defifnition, 10, -10, 0.1, 100, use_decay_lr=True)
matias_function.show_history_GD(history)